In [ ]:
import pandas as pd
import geopandas as gpd
import folium

# Methods: 

from src import folium_visualization_methods as fvm

In [ ]:
predictions_df = pd.read_parquet("../data/proccesed_data/final_predictions_to_visualize.parquet")
predictions_df.head()

terc_code          county  round  turnout_percentage  year
11      0201   bolesławiecki      1               64.91  2030
12      0201   bolesławiecki      2               67.14  2030
24      0202  dzierżoniowski      1               65.44  2030
25      0202  dzierżoniowski      2               70.57  2030
37      0203       głogowski      1               71.22  2030

In [ ]:
geo_spatial = gpd.read_file("../Data/Raw_data/Geo_spacial/county_borders.shp", encoding= "utf-8")
geo_spatial.head()

JPT_KOD_JE JPT_SJR_KO             JPT_NAZWA_  JPT_POWIER JPT_ORGAN_  \
0       0401        POW  powiat aleksandrowski     47461.0       None   
1       2001        POW     powiat augustowski    165937.0       None   
2       2801        POW     powiat bartoszycki    130744.0       None   
3       1001        POW    powiat bełchatowski     96761.0       None   
4       2401        POW       powiat będziński     36431.0       None   

  JPT_KOD__1 JPT_NAZWA1 JPT_ORGAN1 JPT_WAZNA_    IIP_PRZEST  ... WERSJA_DO  \
0       None       None        NZN        NZN  PL.PZGIK.200  ...      None   
1       None       None        NZN        BRK  PL.PZGIK.200  ...      None   
2       None       None        NZN        NZN  PL.PZGIK.200  ...      None   
3       None       None        NZN        NZN  PL.PZGIK.200  ...      None   
4       None       None        NZN        NZN  PL.PZGIK.200  ...      None   

              WAZNY_OD WAZNY_DO           IIP_WERSJA JPT_OPIS     JPT_ID  \
0  2012-09-26T00:00:00     None  2025-02-28T16:25:41     None  2763326.0   
1  2012-09-26T00:00:00     None  2025-02-28T16:25:41     None  2763327.0   
2  2012-09-26T00:00:00     None  2025-06-03T13:11:10     None  2772928.0   
3  2012-09-26T00:00:00     None  2025-01-14T00:00:00     None  2750652.0   
4  2012-09-26T00:00:00     None  2025-07-07T08:35:44     None  2773805.0   

            REGON  Shape_Leng Shape_Area  \
0  91086647100000    1.779400   0.063230   
1  79067090600000    3.720677   0.226346   
2  51074243900000    3.243873   0.180193   
3  59064842200000    2.700353   0.124864   
4  27625494000000    2.026378   0.046071   

                                            geometry  
0  POLYGON ((18.54317 52.8327, 18.54379 52.83357,...  
1  POLYGON ((23.23399 53.95638, 23.23748 53.95596...  
2  POLYGON ((20.82502 54.3601, 20.82502 54.3601, ...  
3  POLYGON ((19.27092 51.2049, 19.27089 51.20493,...  
4  MULTIPOLYGON (((19.35206 50.26668, 19.35211 50...  

[5 rows x 29 columns]

In [ ]:
predictions_df = (predictions_df.pivot_table(
    index=["terc_code", "county"], 
    columns="round", 
    values="turnout_percentage"
    )
    .reset_index()
)

predictions_df.columns.name = None
predictions_df = predictions_df.rename(columns={1: "round_1", 2: "round_2"})

print(predictions_df.head())

  terc_code          county  round_1  round_2
0      0201   bolesławiecki    64.91    67.14
1      0202  dzierżoniowski    65.44    70.57
2      0203       głogowski    71.22    75.39
3      0204        górowski    64.28    70.36
4      0205        jaworski    63.84    66.68


In [ ]:
geo_spatial["geometry"] = geo_spatial["geometry"].simplify(tolerance=0.001, preserve_topology=True)

final_df = geo_spatial.merge(predictions_df, left_on= "JPT_KOD_JE", right_on= "terc_code", how= "inner")

map = folium.Map(location= [52.0, 19.0], zoom_start= 6, tiles= "CartoDB positron")

folium.GeoJson(
    final_df,
    style_function= fvm.style_function,
    highlight_function= fvm.highlight_function,
    tooltip=folium.GeoJsonTooltip(
        fields= ["county", "round_1", "round_2"],
        aliases= ["County:", "Round I (%):", "Round II (%):"],
        localize= True,
        sticky= True,
        style= "font-family: Arial; font-size: 14px; padding: 10px; background-color: white; border: 1px solid black;"
    )
).add_to(map)

# To see the map without downloading the entire project, download it from the visualization directory and open it in a browser. 
# This is due to Github blocking the display of JavaScript-based files in projects.

map

In [ ]:
map.save("../visualization/turnout_prediction_2030_map.html")